In [1]:
import datetime
import os
import pandas as pd
import warnings

from dateutil.relativedelta import relativedelta
from src.features.utils import (
    get_data,
    process_str_data_to_json_requirements,
    read_as_dict,
    get_dataframe_from_dict,
)
from src.data.utils import create_index_for_row_data

In [2]:
warnings.filterwarnings('ignore')

In [3]:
FILE_PATH = './'
PATH  = os.path.join(FILE_PATH, '..',)

In [6]:
def calculate_rolling_window_features(data, days, date_col='DATE', column_value='DROUGHT_INDEX'):
    df = data.copy()
    rolling_df = df.rolling(f'{days}D', on=date_col, min_periods=days//30, closed='left')
    rolling_df_target = rolling_df[column_value]

    df[f'{column_value}__mean__last{days}_days'] = rolling_df_target.mean()
    df[f'{column_value}__std__last{days}_days'] = rolling_df_target.std()
    df[f'{column_value}__max__last{days}_days'] = rolling_df_target.max()
    df[f'{column_value}__min__last{days}_days'] = rolling_df_target.min()
    df[f'{column_value}__median__last{days}_days'] = rolling_df_target.median()
    df[f'{column_value}__kurtosis__last{days}_days'] = rolling_df_target.kurt()
    df[f'{column_value}__skewness__last{days}_days'] = rolling_df_target.skew()
    df[f'{column_value}__range__last{days}_days'] = (
            df[f'{column_value}__max__last{days}_days'] -
            df[f'{column_value}__min__last{days}_days']
    )
    df[f'{column_value}__mean_vs_median__last{days}_days'] = (
            df[f'{column_value}__mean__last{days}_days'] -
            df[f'{column_value}__median__last{days}_days']
    )
    features_cols = [col for col in df.columns if '__' in col]
    return df[features_cols]

def window_feature_generator(data, column_value, *window):
    """

    """
    data_rolling_list = []
    for w in window:
        data_rolling = data.groupby('CVE_CONCATENADA').apply(
            calculate_rolling_window_features,
            days=w,
            column_value=column_value,
        )
        data_rolling = data_rolling.reset_index().set_index('index').drop('CVE_CONCATENADA', axis=1)
        data_rolling_list.append(data_rolling)
    data_rolling__all_features = pd.concat(data_rolling_list, axis=1)
    return data_rolling__all_features

def targets_displaced_data(data, date_col='NEW_DATE', *months):
    """ This function generates a target with the DROUGHT_INDEX as if you can see the future. That is to say:
    What would be the DROUGHT INDEX for an specific instance in the future (1 month, 3 months, 6 months, 1 year).
    """
    general_data = data.copy()
    for month in months:
        general_data.set_index(data.index)
        displaced_data = general_data.copy()
        column = f'DISPLACED_DATE{month}_MONTHS'
        target = f'DROUGHT_INDEX_NEXT{month}_MONTHS'
        date_displacement = lambda x: x + relativedelta(months=-month)
        displaced_data[column] = displaced_data[date_col].apply(date_displacement)
        print(displaced_data[column].head())
        target_df = create_index_for_row_data(displaced_data, column).copy()
        target_df.rename(columns={'DROUGHT_INDEX': target}, inplace=True)
        general_data[target] = target_df[target]
    drought_targets = [drought_target for drought_target in general_data.columns if 'DROUGHT_INDEX' in drought_target]
    return general_data[drought_targets]

def function_for_neighbour_features(row, data):
    grouped_dfs = []
    statistic_value_list = ['mean', 'std', 'min', 'max', 'median']
    for neighbour_num in row.index:
        if not 'neighbour' in neighbour_num:
            continue
        df_grouped = data[
            data.CVE_CONCATENADA.isin(
                row[neighbour_num]
            )
        ].drop('CVE_CONCATENADA',axis=1).groupby('NEW_DATE')
        all_statistics_list = []
        for statistic in statistic_value_list:
            df_grouped_statistic = df_grouped.agg(statistic)
            df_grouped_statistic.columns = [f'{col}__{neighbour_num}_{statistic}' for col in df_grouped_statistic.columns]
            all_statistics_list.append(df_grouped_statistic)
        all_statistics_df = pd.concat(all_statistics_list, axis=1)
        all_statistics_df['CVE_CONCATENADA'] = row.name
        all_statistics_df.reset_index(inplace=True)
        grouped_dfs.append(all_statistics_df)
    final_neighbour_features_result = pd.concat(grouped_dfs, axis=1)
    final_neighbour_features_result = final_neighbour_features_result.loc[:,~final_neighbour_features_result.columns.duplicated()].copy()
    return final_neighbour_features_result

def complement_neighbour_features(data, alpha=1, beta=2):
    df = data.copy()
    statistic_value_list = ['mean', 'std', 'min', 'max', 'median']
    possible_candidates = list(set([col.rsplit('__',1)[0] for col in df.columns.to_list()]))
    new_feature_list = []
    for val in possible_candidates:
        for stat in statistic_value_list:
            new_feature = f'{val}__{beta}vs{alpha}_{stat}'
            alpha_feature = f'{val}__{beta}_{stat}'
            beta_feature = f'{val}__{alpha}_{stat}'
            df[new_feature] = df[beta_feature]-df[alpha_feature]
            new_feature_list.append(new_feature)
    return df[new_feature_list]

def process_daily_information(daily_information):
    daily_information.loc[:,'time'] = pd.to_datetime(daily_information['time'])
    daily_information = daily_information[daily_information.time > pd.to_datetime('2003-01-01')]
    daily_information['sunrise'] = pd.to_datetime(daily_information['sunrise'])
    daily_information['sunset'] = pd.to_datetime(daily_information['sunset'])
    daily_information.loc[:,'day_duration'] = (daily_information['sunset'] - daily_information['sunrise']).dt.seconds
    daily_information.loc[:,'temperature_range'] = daily_information['temperature_2m_max'] - daily_information['temperature_2m_min']
    daily_information.loc[:,'temperature_max_apparent_range'] = daily_information['temperature_2m_max'] - daily_information['apparent_temperature_max']
    daily_information.loc[:,'temperature_min_apparent_range'] = daily_information['temperature_2m_min'] - daily_information['apparent_temperature_min']
    daily_information.loc[:,'temperature_mean_apparent_range'] = daily_information['temperature_2m_mean'] - daily_information['apparent_temperature_mean']
    daily_information.rename(columns={'time':'DATE'}, inplace=True)
    daily_information.loc[:,'NEW_DATE'] = daily_information['DATE'] + datetime.timedelta(days=10)
    daily_information.drop(['sunrise', 'sunset'], axis=1, inplace=True)
    daily_information.loc[:,'CVE_CONCATENADA'] = 'test'
    daily_information = create_index_for_row_data(daily_information, 'DATE')
    return daily_information

def calculate_rolling_window_meteorological_features(df):
    features_to_rolling_compute = [
        'temperature_2m_max',
        'temperature_2m_min',
        'temperature_2m_mean',
        'apparent_temperature_max',
        'apparent_temperature_min',
        'apparent_temperature_mean',
        'shortwave_radiation_sum',
        'precipitation_sum',
        'rain_sum',
        'precipitation_hours',
        'day_duration',
        'temperature_range',
        'temperature_max_apparent_range',
        'temperature_min_apparent_range',
        'temperature_mean_apparent_range',
    ]
    features_last_days = []
    for col in features_to_rolling_compute:
        features_last_days.append(calculate_rolling_window_features(df, days=90, date_col='DATE', column_value=col))
        features_last_days.append(calculate_rolling_window_features(df, days=180, date_col='DATE', column_value=col))
        features_last_days.append(calculate_rolling_window_features(df, days=360, date_col='DATE', column_value=col))
    results = pd.concat(features_last_days, axis=1)
    results['NEW_DATE'] = df['NEW_DATE']
    return results[results.NEW_DATE.isin(drought_data.NEW_DATE.unique())]

def meteorological_process(initial_dict):
    initial_dict = read_as_dict(initial_dict, specific_key='daily')
    df = get_dataframe_from_dict(initial_dict)
    daily_info = process_daily_information(df)
    rwmf = calculate_rolling_window_meteorological_features(daily_info)
    return rwmf

In [5]:
    DATA_PATH = 'data/'
    DROUGHT_DATA_INTERIM_PATH = os.path.join(PATH, DATA_PATH, 'interim','drougt_data.csv')
    NEIGHBOUR_DATA_INTERIM_PATH = os.path.join(PATH, DATA_PATH, 'interim','neighbour_data.csv')
    METEOROLOGICAL_DATA_RAW_PATH = os.path.join(PATH,DATA_PATH, 'raw', 'meteorological_information.csv')
    METEOROLOGICAL_DATA_FEATURES = os.path.join(PATH, DATA_PATH, 'interim', 'meteorological_data_features.csv')

    DROUGHT_DATA_FEATURES_PATH = os.path.join(PATH, DATA_PATH, 'interim','drougt_data_features.csv')
    DROUGHT_DATA_TARGETS_PATH = os.path.join(PATH, DATA_PATH, 'interim','drougt_data_targets.csv')
    DROUGHT_DATA_NEIGHBOUR_FEATURES_PATH = os.path.join(PATH, DATA_PATH, 'interim', 'drought_data_neighbour_features.csv')

    drought_data = get_data(DROUGHT_DATA_INTERIM_PATH)
    neighbour_data = get_data(NEIGHBOUR_DATA_INTERIM_PATH)
    meteorological_data = get_data(METEOROLOGICAL_DATA_RAW_PATH)

In [7]:
    # Get targets
    targets = targets_displaced_data(drought_data, 'NEW_DATE', 1, 3, 6, 12)
    targets.to_csv(DROUGHT_DATA_TARGETS_PATH)
    
    drought_data_features = window_feature_generator(drought_data, 'DROUGHT_INDEX', 90, 180, 360)
    drought_data_features.to_csv(DROUGHT_DATA_FEATURES_PATH)

index
2003-01-28__1001   2002-12-28
2003-01-28__1002   2002-12-28
2003-01-28__1003   2002-12-28
2003-01-28__1004   2002-12-28
2003-01-28__1005   2002-12-28
Name: DISPLACED_DATE1_MONTHS, dtype: datetime64[ns]
index
2003-01-28__1001   2002-10-28
2003-01-28__1002   2002-10-28
2003-01-28__1003   2002-10-28
2003-01-28__1004   2002-10-28
2003-01-28__1005   2002-10-28
Name: DISPLACED_DATE3_MONTHS, dtype: datetime64[ns]
index
2003-01-28__1001   2002-07-28
2003-01-28__1002   2002-07-28
2003-01-28__1003   2002-07-28
2003-01-28__1004   2002-07-28
2003-01-28__1005   2002-07-28
Name: DISPLACED_DATE6_MONTHS, dtype: datetime64[ns]
index
2003-01-28__1001   2002-01-28
2003-01-28__1002   2002-01-28
2003-01-28__1003   2002-01-28
2003-01-28__1004   2002-01-28
2003-01-28__1005   2002-01-28
Name: DISPLACED_DATE12_MONTHS, dtype: datetime64[ns]


In [8]:
    meteorological_data['CVE_CONCATENADA'] = meteorological_data['CVEGEO']
    meteorological_data_cols = ['CVE_CONCATENADA', 'meteorological_information']
    meteorological_data = meteorological_data[meteorological_data_cols]
    meteorological_data.set_index('CVE_CONCATENADA', inplace=True)
    meteorological_info = meteorological_data.meteorological_information.apply(meteorological_process)
    meteorological_info_dict = meteorological_info.to_dict()
    gather_all = []

In [18]:
    for key in meteorological_info_dict.keys():
        meteorological_info_dict[key]['CVE_CONCATENADA'] = key
        f = create_index_for_row_data(meteorological_info_dict[key], 'NEW_DATE')
        gather_all.append(f)

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

...

/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  meteorological_info_dict[key]['CVE_CONCATENADA'] = key
/mnt/c/Users/dhdzm/Documents/projects/seguia/seguia/src/data/utils.py:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  df['index'] = (
/tmp/ipykernel_431/2962812645.py:2: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a 

In [35]:
    meteorological_data_features = pd.concat(gather_all)


In [36]:
    features = pd.concat([drought_data_features, meteorological_data_features], axis=1)


In [ ]:
    neighbour_features_series = neighbour_data.apply(function_for_neighbour_features, data=features, axis=1)
    neighbour_features = pd.concat(neighbour_features_series.to_list())
    neighbour_features.NEW_DATE = pd.to_datetime(neighbour_features.NEW_DATE)
    neighbour_features = create_index_for_row_data(neighbour_features, 'NEW_DATE')
    neighbour_features.drop(['NEW_DATE', 'CVE_CONCATENADA'], axis=1, inplace=True)
    neighbour_features_12 = complement_neighbour_features(neighbour_features, 1, 2)
    neighbour_features_13 = complement_neighbour_features(neighbour_features, 1, 3)
    neighbour_features_23 = complement_neighbour_features(neighbour_features, 2, 3)
    all_neighbour_features = pd.concat(
        [neighbour_features, neighbour_features_12, neighbour_features_13,neighbour_features_23], axis=1)

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

...

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df['CVE_CONCATENADA'] = row.name
/tmp/ipykernel_431/4161404399.py:77: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_statistics_df.reset_index(inplace=True)
/tmp/ipykernel_431/4161404399.py:76: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented

In [33]:
neighbour_data['neighbours__1'] = neighbour_data.neighbours__1.apply(json.loads)
neighbour_data['neighbours__2'] = neighbour_data.neighbours__2.apply(json.loads)
neighbour_data['neighbours__3'] = neighbour_data.neighbours__3.apply(json.loads)

In [29]:
import json